# **THU THẬP DỮ LIỆU**
## Ý tưởng 
    Nhóm muốn thu thập thông tin về các yếu tố ảnh hưởng đến giá nhà (Bao gồm: chung cư, nhà đất, ...) tại thành phố Hồ Chí Minh
    VD: Diện tích, số phòng ngủ, phòng tắm, ... và các tiện ích liên quan
## Thực hiện
    Nhóm đã tìm được trang web khá phù hợp để thu thập dữ liệu
    'https://rever.vn'
    

In [1]:
# IMPORT THƯ VIỆN
import numpy
from bs4 import BeautifulSoup
import urllib.request
from protego import Protego
import requests
from requests import Session
import lxml
import re
import pandas as pd
from time import sleep

In [2]:
# Khởi tạo phương thức get
s = Session()
headers = {'User-Agent': 'Mozilla/5.0 (X11; Linux x86_64) '\
                         'AppleWebKit/537.36 (KHTML, like Gecko) '\
                         'Chrome/75.0.3770.80 Safari/537.36'}
# Add headers
s.headers.update(headers)
# we can use s as we do requests
# s.get(...)


Ellipsis

#### Kiểm tra robots.txt
    Dùng thư viện protego để kiểm tra việc thu thập dữ liệu của trang web này có vi phạm không?
    Kết quả trả về True có nghĩa là được phép.

In [3]:
# kiểm tra việc thu thập
base_url = 'https://rever.vn'

r = s.get(base_url + "/robots.txt")
rp = Protego.parse(r.text)
rp.can_fetch(base_url, "*")

True

In [4]:
# Thu thập số trang của phần mua nhà, lưu vào file csv
def get_number_of_pages(url):
    
    """
    Hàm thu thập tất cả trang web của phần mua nhà
    """
    req = s.get(url)
    if req.status_code == requests.codes.ok:
        bs = BeautifulSoup(req.text, 'lxml')
        url_last = bs.findAll('a', class_ = 'btnNext')
        result = re.sub(r'\D', "", url_last[0]['href'])    
        return int(result)


page_urls = set()
num_pages = get_number_of_pages('https://rever.vn/s/ho-chi-minh/mua')

for i in range(1, num_pages+1):
    page_urls.add('https://rever.vn/s/ho-chi-minh/mua?page=' + str(i) +'&search_mode=1')
    
list_page_urls = list(page_urls)
page_urls_df = pd.DataFrame({'URL' : list_page_urls})
page_urls_df.to_csv("PAGEs_urls.csv", sep = '\t')

# Tổng số trang
len(list_page_urls)

352

In [5]:
def crawl_house_one_page(one_page_url):
    """
    Hàm thu thập tất cả url của các căn nhà trong 1 trang
    """
    req = s.get(one_page_url)
    if req.status_code == requests.codes.ok:
        bs = BeautifulSoup(req.text, 'lxml')
        list_pages = bs.findAll('div', class_ = 'group-grid__view')
        
        for house in list_pages:
            house_url = house.find('a')['href']
            house_url = base_url + house_url
            house_urls.add(house_url)

In [6]:
# Thu thập toàn bộ url và lưu vào file csv
house_urls = set()

for page in list_page_urls:
    crawl_house_one_page(page)
    
list_house_urls = list(house_urls)
house_urls_df = pd.DataFrame({'URL' : list_house_urls})
house_urls_df.to_csv("HOUSEs_urls.csv", sep = '\t')


In [7]:
houses_df = pd.read_csv('HOUSEs_urls.csv', sep = '\t')
len(houses_df)
list_house_urls

['https://rever.vn/mua/ban-can-ho-saigon-south-residence-2pn-tang-cao-ban-cong-dong-bac-view-song',
 'https://rever.vn/mua/nha-pho-mat-tien-quan-8-view-song-huong-tay-bac',
 'https://rever.vn/mua/can-ho-one-verandah-day-du-noi-that-san-lot-go-view-thanh-pho',
 'https://rever.vn/mua/ban-nha-3-tang-hem-ton-dan-quan-4-so-hong-khong-co-noi-that',
 'https://rever.vn/mua/can-ho-topaz-elite-huong-dong-nam-view-thanh-pho',
 'https://rever.vn/mua/can-ho-vinhomes-grand-park-noi-that-co-ban-tang-trung',
 'https://rever.vn/mua/ban-hoac-cho-thue-can-ho-sunrise-city-2pn-thap-w2-khu-central-plaza-dien-tich-76m2-day-du-noi-that',
 'https://rever.vn/mua/can-ho-riviera-point-phong-ngu-lot-san-go-view-thanh-pho-sam-uat',
 'https://rever.vn/mua/can-ho-vinhomes-grand-park-tang-cao-don-view-ngoai-khu',
 'https://rever.vn/mua/can-ho-an-gia-riverside-tang-cao-view-song-sai-gon',
 'https://rever.vn/mua/can-ho-opal-boulevard-tang-35-view-thoang-mat-2-phong-ngu',
 'https://rever.vn/mua/ban-can-ho-officetel-orcha

In [8]:
def get_info_house(one_house_url):
    '''
    get house's info from page
        input: house's url
        output: house's data
    '''
    data = {}

    req = s.get(one_house_url)
    if req.status_code == requests.codes.ok:
        bs = BeautifulSoup(req.text, 'lxml')
        left_house = bs.findAll('p', class_ = 'left')
        right_house = bs.findAll('p', class_ = 'right')
        
        list_attributes = []
        for attribute in left_house:
            list_attributes.append(attribute.text)
            
            
        list_values = []
        for value in right_house:
            if value.text != '':
                list_values.append(value.text)
            else:
                check = value['class']
                if any("close" in s for s in check):
                    list_values.append('No')
                elif any("check" in s for s in check):
                    list_values.append('Yes')
                    
                    
        for i in range(0, len(list_attributes)):
            data[list_attributes[i]] = list_values[i]
    
    return data

In [9]:
list_all_houses = []

for house_url in list_house_urls:
    data_dict = {}
    data_dict = get_info_house(house_url)
    print(data_dict)
#     if not list_all_houses:
#         list_all_houses.append(list(data_dict.keys()))
#     list_all_houses.append(data_dict)
    

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Số tầng': '28', 'Diện tích': '71.42 m²', 'Diện tích sử dụng': '65.16 m²', 'Tình hình nội thất': 'Không có nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Saigon South Residence', 'Giá bán': '3.15 tỷ', 'Thời gian Xây dựng': '26/12/2019', 'Ban công': 'Yes', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'Yes', 'Quầy minibar': 'No', 'Tầng hầm': 'Yes', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'Yes', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', '

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '76 m²', 'Dự án': 'Sunrise City', 'Tháp': 'W2 Khu Central Plaza', 'Giá bán': '3.9 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'Yes', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'Yes', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'Yes', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'Yes', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'Yes', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'Yes', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy hút mùi': 'No', 'Cảm biến cháy': 'No', 'Tủ lạnh': 'No', 'Bếp ga, bếp từ': 'No', 'Máy giặt': 'No', 'Má

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '1', 'Phòng tắm': '1', 'Số tầng': '15', 'Diện tích': '38.5 m²', 'Diện tích sử dụng': '38.5 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Sunrise CityView', 'Tháp': 'B', 'Giá bán': '2.01 tỷ', 'Ban công': 'Yes', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'Yes', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'Yes', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'Yes', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'Yes', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'Yes', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'Yes', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'Yes', 'Đệm, chăn, gối': 'Yes', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'Yes', 'Bàn trang điểm': 'No', 'TV'

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Số tầng': '9', 'Diện tích': '76 m²', 'Diện tích sử dụng': '76 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'Sổ hồng', 'Giá bán': '3.4 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy hút mùi': 'No', 'Cảm biến cháy': 'No', 'Tủ lạnh'

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '76.6 m²', 'Diện tích sử dụng': '71.6 m²', 'Tình hình nội thất': 'Không có nội thất', 'Dự án': 'Sunrise CityView', 'Tháp': 'A', 'Giá bán': '3.45 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy hút mùi': 'No', 'Cảm biến cháy': 'No', 'Tủ l

...

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Số tầng': '2', 'Diện tích': '70 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Dự án': 'Sunrise Riverside', 'Giá bán': '2.9 tỷ', 'Ban công': 'Yes', 'Phòng cho giúp việc': 'Yes', 'Sân vườn': 'Yes', 'Phòng giải trí': 'Yes', 'Chỗ đậu xe hơi': 'Yes', 'Hồ bơi riêng': 'Yes', 'Quầy minibar': 'Yes', 'Tầng hầm': 'Yes', 'Góc làm việc': 'Yes', 'Nhà kho': 'Yes', 'Nuôi thú cưng': 'Yes', 'Gym': 'Yes', 'Bàn ghế phòng khách': 'Yes', 'Kệ TV': 'Yes', 'Bộ bàn ăn và ghế': 'Yes', 'Đảo bếp\n': 'Yes', 'Đèn trang trí': 'Yes', 'Bếp ướt': 'Yes', 'Bếp khô': 'Yes', 'Tủ bếp trên\n': 'Yes', 'Tủ bếp dưới\n': 'Yes', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy hút mùi': 'No', 'Cảm biến cháy': 'No', 'Tủ lạnh': 'No', 

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '2', 'Phòng tắm': '2', 'Diện tích': '69 m²', 'Diện tích sử dụng': '63 m²', 'Tình hình nội thất': 'Không có nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Vinhomes Grand Park', 'Tháp': 'S1.06', 'Giá bán': '2.58 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy hút mùi':

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '1', 'Phòng tắm': '1', 'Diện tích': '36 m²', 'Diện tích sử dụng': '36 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Loại chủ quyền': 'HĐ mua bán', 'Dự án': 'Vinhomes Central Park', 'Giá bán': '2.95 tỷ', 'Ban công': 'No', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'No', 'Hồ bơi riêng': 'No', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'No', 'Nhà kho': 'No', 'Nuôi thú cưng': 'No', 'Gym': 'No', 'Bàn ghế phòng khách': 'No', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'No', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'No', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'No', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'No', 'Bàn trang điểm': 'No', 'TV': 'No', 'Máy hút mùi': 'No', 'Cảm biến 

{'Loại hình': 'Căn hộ', 'Phòng ngủ': '3', 'Phòng tắm': '3', 'Diện tích': '171 m²', 'Tình hình nội thất': 'Đầy đủ nội thất', 'Mục đích sử dụng': 'Ở', 'Dự án': 'The Estella An Phú', 'Giá bán': '7.55 tỷ', 'Thời gian bắt đầu bán': '09/06/2018', 'Ban công': 'Yes', 'Phòng cho giúp việc': 'No', 'Sân vườn': 'No', 'Phòng giải trí': 'No', 'Chỗ đậu xe hơi': 'Yes', 'Hồ bơi riêng': 'Yes', 'Quầy minibar': 'No', 'Tầng hầm': 'No', 'Góc làm việc': 'Yes', 'Nhà kho': 'No', 'Nuôi thú cưng': 'Yes', 'Gym': 'Yes', 'Bàn ghế phòng khách': 'Yes', 'Kệ TV': 'No', 'Bộ bàn ăn và ghế': 'Yes', 'Đảo bếp\n': 'No', 'Đèn trang trí': 'No', 'Bếp ướt': 'No', 'Bếp khô': 'No', 'Tủ bếp trên\n': 'No', 'Tủ bếp dưới\n': 'No', 'Sàn gỗ': 'No', 'Tủ âm tường': 'No', 'Tủ treo đồ / tủ quần áo': 'Yes', 'Tủ kê đầu giường': 'No', 'Đèn trần': 'No', 'Đèn bàn': 'No', 'Giường\n': 'Yes', 'Đệm, chăn, gối': 'No', 'Tủ giày dép': 'No', 'Bồn tắm': 'No', 'Kệ sách': 'No', 'Bàn làm việc': 'Yes', 'Bàn trang điểm': 'Yes', 'TV': 'No', 'Máy hút mùi': 'No'

KeyboardInterrupt: 